In [1]:
import polars as pl

In [2]:
df = pl.read_parquet(r"F:\LPU\Data\Datasets\Hate-Speech Classification\hpc_batch\final_df\vectorized_df.parquet") 

In [3]:
print(df.schema)

Schema({'Content': String, 'Label': Int64, 'Tokens_Content': List(String), 'Processed_Content': List(String), 'Vector_Content': List(Array(Float32, shape=(300,)))})


In [4]:
df.head() 

shape: (5, 5)
┌──────────────────────┬───────┬──────────────────────┬──────────────────────┬─────────────────────┐
│ Content              ┆ Label ┆ Tokens_Content       ┆ Processed_Content    ┆ Vector_Content      │
│ ---                  ┆ ---   ┆ ---                  ┆ ---                  ┆ ---                 │
│ str                  ┆ i64   ┆ list[str]            ┆ list[str]            ┆ list[array[f32,     │
│                      ┆       ┆                      ┆                      ┆ 300]]               │
╞══════════════════════╪═══════╪══════════════════════╪══════════════════════╪═════════════════════╡
│ denial of normal the ┆ 1     ┆ ["denial", "of", …   ┆ ["denial", "normal", ┆ [[-0.304153,        │
│ con be as…           ┆       ┆ "retard"]            ┆ … "retard…           ┆ -0.501737, … 0.78…  │
│ just by being able   ┆ 1     ┆ ["just", "by", …     ┆ ["able", "tweet", …  ┆ [[-0.729719,        │
│ to tweet th…         ┆       ┆ "vagina"]            ┆ "vagina"]            ┆ 0.40294, … 0.1556…  │
│ that is retarded you ┆ 1     ┆ ["that", "is", …     ┆ ["retard", "cute", … ┆ [[-2.177103,        │
│ too cute …           ┆       ┆ "life"]              ┆ "life"]              ┆ 0.183218, … -0.49…  │
│ thought of a real    ┆ 1     ┆ ["thought", "of", …  ┆ ["think", "real", …  ┆ [[-0.442838,        │
│ badass mongo…        ┆       ┆ "be"]                ┆ "soon"]              ┆ 1.159951, … -0.58…  │
│ afro american basho  ┆ 1     ┆ ["afro", "american", ┆ ["afro", "american", ┆ [[-1.056091,        │
│                      ┆       ┆ "basho"]             ┆ "basho"]             ┆ -0.674072, … -1.9…  │
└──────────────────────┴───────┴──────────────────────┴──────────────────────┴─────────────────────┘

In [118]:
data = df.select(pl.col(["Vector_Content","Label"]))
data 

shape: (726_119, 2)
┌─────────────────────────────────┬───────┐
│ Vector_Content                  ┆ Label │
│ ---                             ┆ ---   │
│ list[array[f32, 300]]           ┆ i64   │
╞═════════════════════════════════╪═══════╡
│ [[-0.304153, -0.501737, … 0.78… ┆ 1     │
│ [[-0.729719, 0.40294, … 0.1556… ┆ 1     │
│ [[-2.177103, 0.183218, … -0.49… ┆ 1     │
│ [[-0.442838, 1.159951, … -0.58… ┆ 1     │
│ [[-1.056091, -0.674072, … -1.9… ┆ 1     │
│ …                               ┆ …     │
│ [[0.099826, 0.173445, … -0.088… ┆ 1     │
│ [[1.366367, 0.143709, … -0.533… ┆ 1     │
│ [[-0.184502, 0.007078, … -1.89… ┆ 1     │
│ [[-0.718526, -0.147325, … -0.6… ┆ 1     │
│ [[-0.184502, 0.007078, … -1.89… ┆ 1     │
└─────────────────────────────────┴───────┘

In [77]:
print(type(data["Vector_Content"][0]))

<class 'polars.series.series.Series'>


In [79]:
len(data)

726119

In [85]:
import numpy as np

divider = (round((len(df) * 0.2)))

test_df = df.slice(0, divider)
train_df = df.slice(divider, len(df))

X_train = (train_df.select(pl.col("Vector_Content")))
y_train = np.ravel(train_df.select(pl.col("Label")))

X_test = (test_df.select(pl.col("Vector_Content")))
y_test = np.ravel(test_df.select(pl.col("Label"))) 


print(len(X_train))
print(len(X_test))


580895
145224


In [86]:
X_train = X_train.to_numpy().reshape(-1, 1)
X_test = X_test.to_numpy().reshape(-1, 1)

print(type(X_train))
print(X_train.shape)

<class 'numpy.ndarray'>
(580895, 1)


In [87]:
print(X_train.shape)
print(X_test.shape)

print(y_train.shape)
print(y_test.shape)

(580895, 1)
(145224, 1)
(580895,)
(145224,)


In [88]:
print(X_train[:5])
print(y_train[:5])

[[array([[ 1.8205235 ,  1.0661037 , -0.71777177, ..., -0.51337403,
           0.73966914,  0.3091713 ],
         [ 0.23467267, -0.27089298, -0.5570078 , ...,  0.3959005 ,
           0.6414915 , -1.040077  ],
         [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
          -2.1329906 , -1.1171429 ],
         ...,
         [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
          -2.1329906 , -1.1171429 ],
         [-1.0433347 ,  0.8699964 ,  1.4821112 , ..., -0.7343741 ,
           1.5424325 , -2.3922253 ],
         [-0.08398671,  0.23153958, -0.01149722, ..., -0.5306966 ,
          -0.15784127,  0.09090139]], dtype=float32)              ]
 [array([[-1.1374826 ,  0.6928228 ,  0.5786205 , ...,  0.9941442 ,
          -0.27995363,  0.03319994],
         [ 0.04240718,  1.1792461 , -1.437097  , ...,  0.7289516 ,
          -0.4775798 ,  1.3511053 ],
         [-0.38211438, -0.4193859 , -0.28780833, ...,  0.7307229 ,
          -0.3103435 ,  0.7111875 ],
         [-0.072491

In [90]:
print(X_train.shape)
print(type(X_train))

print(y_train.shape)
print(type(y_train))

(580895, 1)
<class 'numpy.ndarray'>
(580895,)
<class 'numpy.ndarray'>


In [91]:
print(X_train[0])

[array([[ 1.8205235 ,  1.0661037 , -0.71777177, ..., -0.51337403,
          0.73966914,  0.3091713 ],
        [ 0.23467267, -0.27089298, -0.5570078 , ...,  0.3959005 ,
          0.6414915 , -1.040077  ],
        [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
         -2.1329906 , -1.1171429 ],
        ...,
        [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
         -2.1329906 , -1.1171429 ],
        [-1.0433347 ,  0.8699964 ,  1.4821112 , ..., -0.7343741 ,
          1.5424325 , -2.3922253 ],
        [-0.08398671,  0.23153958, -0.01149722, ..., -0.5306966 ,
         -0.15784127,  0.09090139]], dtype=float32)              ]


In [103]:
print(X_train[0].squeeze())


[[ 1.8205235   1.0661037  -0.71777177 ... -0.51337403  0.73966914
   0.3091713 ]
 [ 0.23467267 -0.27089298 -0.5570078  ...  0.3959005   0.6414915
  -1.040077  ]
 [-0.68998665  0.95594764  1.0666867  ...  0.8244816  -2.1329906
  -1.1171429 ]
 ...
 [-0.68998665  0.95594764  1.0666867  ...  0.8244816  -2.1329906
  -1.1171429 ]
 [-1.0433347   0.8699964   1.4821112  ... -0.7343741   1.5424325
  -2.3922253 ]
 [-0.08398671  0.23153958 -0.01149722 ... -0.5306966  -0.15784127
   0.09090139]]


In [ ]:
def rem_X_dim(row):                  
    return row.squeeze()             
                                     
for i in range(len(X_train)):        
    X_train[i] = X_train[i].squeeze()

In [106]:
print(X_train.shape)
print(X_train[0])


(580895, 1)
[array([[ 1.8205235 ,  1.0661037 , -0.71777177, ..., -0.51337403,
          0.73966914,  0.3091713 ],
        [ 0.23467267, -0.27089298, -0.5570078 , ...,  0.3959005 ,
          0.6414915 , -1.040077  ],
        [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
         -2.1329906 , -1.1171429 ],
        ...,
        [-0.68998665,  0.95594764,  1.0666867 , ...,  0.8244816 ,
         -2.1329906 , -1.1171429 ],
        [-1.0433347 ,  0.8699964 ,  1.4821112 , ..., -0.7343741 ,
          1.5424325 , -2.3922253 ],
        [-0.08398671,  0.23153958, -0.01149722, ..., -0.5306966 ,
         -0.15784127,  0.09090139]], dtype=float32)              ]


In [120]:
data

shape: (726_119, 2)
┌─────────────────────────────────┬───────┐
│ Vector_Content                  ┆ Label │
│ ---                             ┆ ---   │
│ list[array[f32, 300]]           ┆ i64   │
╞═════════════════════════════════╪═══════╡
│ [[-0.304153, -0.501737, … 0.78… ┆ 1     │
│ [[-0.729719, 0.40294, … 0.1556… ┆ 1     │
│ [[-2.177103, 0.183218, … -0.49… ┆ 1     │
│ [[-0.442838, 1.159951, … -0.58… ┆ 1     │
│ [[-1.056091, -0.674072, … -1.9… ┆ 1     │
│ …                               ┆ …     │
│ [[0.099826, 0.173445, … -0.088… ┆ 1     │
│ [[1.366367, 0.143709, … -0.533… ┆ 1     │
│ [[-0.184502, 0.007078, … -1.89… ┆ 1     │
│ [[-0.718526, -0.147325, … -0.6… ┆ 1     │
│ [[-0.184502, 0.007078, … -1.89… ┆ 1     │
└─────────────────────────────────┴───────┘

In [121]:
def flatten_vectors(lst):
    print(lst)
    return np.concatenate(lst)

# Apply flattening to the 'Vector_Content' column
data = data.with_columns(pl.col("Vector_Content").map_elements(flatten_vectors, return_dtype=pl.Array(pl.Float32, 300)))

shape: (8,)
Series: '' [array[f32, 300]]
[
	[-0.304153, -0.501737, … 0.784346]
	[-2.171593, 1.819738, … 1.855632]
	[0.078656, 0.174888, … 1.117541]
	[0.308504, 0.073026, … -0.714389]
	[-0.192182, -0.925256, … -1.736569]
	[0.113477, 0.165886, … -0.118165]
	[-0.448441, 0.188781, … 0.115838]
	[-2.177103, 0.183218, … -0.499671]
]shape: (33,)
Series: '' [array[f32, 300]]
[
	[0.151726, 0.011622, … -0.32527]
	[-0.033387, 0.094264, … 0.043353]
	[-0.201457, 0.160241, … 0.236301]
	[1.67503, 0.522968, … -0.810711]
	[-1.373698, -0.72277, … -0.186909]
	…
	[-0.10786, -0.879422, … -0.342684]
	[-0.201457, 0.160241, … 0.236301]
	[-0.033387, 0.094264, … 0.043353]
	[-0.433669, 1.492892, … 0.523425]
	[0.09643, -1.335862, … 0.756954]
]

shape: (5,)
Series: '' [array[f32, 300]]
[
	[-1.803762, 0.036292, … -1.89968]
	[-0.149784, 0.012655, … -0.11267]
	[-0.438227, -1.110197, … 0.679805]
	[-0.078739, 0.530278, … -1.525059]
	[0.69587, 0.828068, … -0.687904]
]
shape: (8,)
Series: '' [array[f32, 300]]
[
	[-0.72971

PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'ValueError'>, value: ValueError('need at least one array to concatenate'), traceback: Some(<traceback object at 0x0000028F54D89D80>) }

shape: (14,)
Series: '' [array[f32, 300]]
[
	[-0.300712, 1.128512, … -0.086525]
	[-0.354928, -1.650167, … 1.387265]
	[0.222696, 0.290478, … -0.051775]
	[0.133669, 0.023128, … 0.039313]
	[-0.085087, -0.330606, … -0.155169]
	…
	[-0.169648, -0.179317, … 0.001645]
	[0.0486, 0.230957, … -0.068107]
	[0.250377, 0.245352, … -0.114525]
	[-0.015655, 0.135429, … -0.024335]
	[-0.859653, 1.247341, … -0.033096]
]
shape: (9,)
Series: '' [array[f32, 300]]
[
	[-0.180684, 1.212917, … 0.54582]
	[-1.352282, 0.073566, … 0.792392]
	[-1.691301, -1.018317, … -1.034729]
	[-0.085087, -0.330606, … -0.155169]
	[-1.691301, -1.018317, … -1.034729]
	[0.275336, 0.026523, … 0.076845]
	[0.574016, -0.463507, … -0.432795]
	[0.172991, 0.21207, … 0.503729]
	[-0.22764, 0.158012, … -0.08891]
]
shape: (6,)
Series: '' [array[f32, 300]]
[
	[-1.691301, -1.018317, … -1.034729]
	[0.141507, -0.176856, … -0.695387]
	[-0.372338, -0.957442, … 0.738619]
	[0.934779, 0.660737, … -0.029314]
	[-0.208495, -1.797946, … 0.535897]
	[1.181523, 

PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'ValueError'>, value: ValueError('need at least one array to concatenate'), traceback: Some(<traceback object at 0x0000028F5620CD40>) }

shape: (9,)
Series: '' [array[f32, 300]]
[
	[0.560789, -0.654039, … -0.856583]
	[-0.10786, -0.879422, … -0.342684]
	[0.558953, 0.280884, … -0.628818]
	[0.280199, 0.420897, … 0.233082]
	[0.417933, -0.546273, … -0.171258]
	[-0.10786, -0.879422, … -0.342684]
	[-0.070064, 0.151906, … -0.086448]
	[-0.718526, -0.147325, … -0.672965]
	[-0.462533, 1.322494, … -1.185939]
]
shape: (60,)
Series: '' [array[f32, 300]]
[
	[-0.349085, -0.464233, … -0.139689]
	[-0.031645, 0.058764, … 0.011169]
	[-0.078739, 0.530278, … -1.525059]
	[-0.500584, -0.541736, … -0.173175]
	[-0.810854, -0.315731, … -2.217332]
	…
	[0.065256, 0.272873, … 0.193028]
	[0.165685, 1.702664, … 1.833567]
	[-0.436969, -0.369909, … -0.708953]
	[-1.848946, 1.665252, … -0.108775]
	[-0.014123, -0.084645, … -0.008705]
]
shape: (32,)
Series: '' [array[f32, 300]]
[
	[0.140543, -0.619639, … -0.93768]
	[1.165411, 0.878256, … -1.573223]
	[0.558953, 0.280884, … -0.628818]
	[0.036882, 0.032574, … 0.064787]
	[-0.718526, -0.147325, … -0.672965]
	…
	

PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'ValueError'>, value: ValueError('need at least one array to concatenate'), traceback: Some(<traceback object at 0x0000028F3A586C00>) }

PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'ValueError'>, value: ValueError('need at least one array to concatenate'), traceback: Some(<traceback object at 0x0000028F5620CD40>) }

In [114]:
data.head()

<Expr ['col("Vector_Content").map_list…'] at 0x28F54436030>

In [107]:
from  sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report
model = LogisticRegression()

model.fit(X_train, y_train)
y_pred = model.predict(X_test)
print(classification_report(y_true=y_test, y_pred=y_pred))

ValueError: setting an array element with a sequence.